In [3]:
import sys
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# auto-reload library if developing library functionalities
%reload_ext autoreload
%autoreload 2
# Add the old-can-decoder-c56d4fe6 directory to sys.path
sys.path.append(os.path.abspath('old-can-decoder-c56d4fe6'))

# import library
from PandaCANDecoder.decoder import Decoder as OldDecoder
from can_decoder.decoder import Decoder

In [4]:
decoder = Decoder("./data/SampleRoadAcceleration_v2.csv")

# Generate message objects

byte_filters = {
    "18DA10F1": ["1", "2", "3", "4",'5'],
    "18DAF110": ["1", "2", "3", "4",'5'],
    "18DAF218": ["1", "2", "3", "4",'5'],
    "18DA18F2": ["1", "2", "3", "4",'5'],
}

decoder.generate_msgs(byte_filters=byte_filters)


Generated 910 messages


In [5]:
## Dynamic filtering: if byte 1 is 0 we should discard byte 5
for msg in decoder.msgs:
    if msg.msg_byte_filter is not None:
        if msg.msg_byte_filter['1'] != 0:
            msg.msg_byte_filter.pop('5', None)
            # Remove duplicates

# Remove duplicate messages with same msg_id and identical msg_byte_filter after discarding byte 5
unique_msgs = []
seen = set()
for msg in decoder.msgs:
    key = (msg.msg_id, tuple(sorted(msg.msg_byte_filter.items())) if msg.msg_byte_filter else None)
    if key not in seen:
        unique_msgs.append(msg)
        seen.add(key)
decoder.msgs = unique_msgs

In [6]:
# Generate message time series data

decoder.generate_msg_ts_data(rewrite=True)  

In [26]:
decoder.calculate_signals(
        tokenization_method='conditional_bit_flip',
        signedness_method='msb_classifier',
        alpha1=0.01,
        alpha2=0.5, #0.5,
        gamma1=0.2)

In [8]:
decoder.get_message('18DA10F1',[0x3,0x22,1,201])

Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:201] : Length 8 bytes

In [9]:
decoder.msgs

[Message 42A: Length 32 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:201] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:209] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:213] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:2|B4:178] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:2|B4:179] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:2|B4:180] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:2|B4:181] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:3|B4:225] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:3|B4:240] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:29] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:32] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:35] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:1|B4:39] : Length 8 bytes,
 Message 18DA10F1 - Filter [B1:3|B2:34|B3:18|B4:201] : Length 8

In [10]:
decoder.plot_message_from_id('201')

In [11]:
decoder.plot_message_from_id('18DAF218',[0,15,98,0x50,0x22])

In [12]:
f = decoder.plot_signal_from_id('18DAF218',[0,15,98,0x50,0x22], signal_id='SIG_BE_3', return_fig=True)
f['data'][0]['mode'] = 'lines+markers'
f.show()

In [13]:
f = decoder.plot_signal_from_id('201',signal_id='SIG_BE_3', return_fig=True)
f['data'][0]['mode'] = 'lines+markers'
f.show()

## Signal Match testing

In [ ]:
decoder.msgs

[Message: 42A, Signal: S_42A_BE_0, Type: constant , Signed: signed, Length: 13,
 Message: 42A, Signal: S_42A_BE_1, Type: ts , Signed: unsigned, Length: 3,
 Message: 42A, Signal: S_42A_BE_2, Type: constant , Signed: signed, Length: 79,
 Message: 42A, Signal: S_42A_BE_3, Type: ts , Signed: unsigned, Length: 1,
 Message: 42A, Signal: S_42A_BE_4, Type: constant , Signed: signed, Length: 84,
 Message: 42A, Signal: S_42A_BE_5, Type: ts , Signed: unsigned, Length: 10,
 Message: 42A, Signal: S_42A_BE_6, Type: ts , Signed: unsigned, Length: 2,
 Message: 42A, Signal: S_42A_BE_7, Type: constant , Signed: signed, Length: 64,
 Message: 42A, Signal: S_42A_LE_0, Type: constant , Signed: signed, Length: 64,
 Message: 42A, Signal: S_42A_LE_1, Type: ts , Signed: unsigned, Length: 6,
 Message: 42A, Signal: S_42A_LE_2, Type: ts , Signed: unsigned, Length: 2,
 Message: 42A, Signal: S_42A_LE_3, Type: constant , Signed: signed, Length: 4,
 Message: 42A, Signal: S_42A_LE_4, Type: ts , Signed: unsigned, Length

In [32]:
from sklearn.linear_model import LinearRegression

signal_a = decoder.get_signal('18DAF218',[0,15,98,0x50,0x22], 'S_18DAF218_BE_3')
signal_b = decoder.get_signal('201',signal_id='S_201_BE_3')

In [33]:
list([signal_a,signal_b])

[Message: 18DAF218, Signal: S_18DAF218_BE_3, Type: ts , Signed: unsigned, Length: 11,
 Message: 201, Signal: S_201_BE_3, Type: ts , Signed: unsigned, Length: 8]

In [35]:
f = decoder.plot_signals([signal_a,signal_b], return_fig=True,normalized=False)
f['data'][0]['mode'] = 'lines+markers'
f.show()

In [36]:
result = decoder.signal_match(signal_a, signal_b,)
result

(LinregressResult(slope=np.float64(0.1250021459218392), intercept=np.float64(-0.5357254467001695), rvalue=np.float64(0.9998628518261544), pvalue=np.float64(0.0), stderr=np.float64(0.0001193407901337974), intercept_stderr=np.float64(0.0979450869034786)),
 np.float64(0.9997257224619305))

In [37]:
fig = decoder.plot_message_ts_signals(msg_id = '10F', byte_filter_values=None, return_fig=True, normalized=True)
fig.write_html("message_ts_signals.html")

In [38]:
candidates_speed = decoder.find_signal_match(
    signal_a,
    thresh=0.9
)

S_18DAF218_BE_3      --> S_208_BE_9           in 208        , r^2=0.9998
S_18DAF218_BE_3      --> S_208_LE_13          in 208        , r^2=0.9893
S_18DAF218_BE_3      --> S_102_BE_1           in 102        , r^2=0.9998
S_18DAF218_BE_3      --> S_102_BE_19          in 102        , r^2=0.9999
S_18DAF218_BE_3      --> S_102_BE_21          in 102        , r^2=0.9996
S_18DAF218_BE_3      --> S_102_LE_20          in 102        , r^2=0.9978
S_18DAF218_BE_3      --> S_102_LE_23          in 102        , r^2=0.9980
S_18DAF218_BE_3      --> S_102_LE_53          in 102        , r^2=0.9756
S_18DAF218_BE_3      --> S_103_BE_2           in 103        , r^2=0.9998
S_18DAF218_BE_3      --> S_103_BE_5           in 103        , r^2=0.9999
S_18DAF218_BE_3      --> S_103_BE_7           in 103        , r^2=0.9996
S_18DAF218_BE_3      --> S_103_BE_9           in 103        , r^2=0.9995
S_18DAF218_BE_3      --> S_103_LE_15          in 103        , r^2=0.9745
S_18DAF218_BE_3      --> S_103_LE_18          in 10

In [39]:
f = decoder.plot_signal_matches(signal_a, candidates_speed, return_fig=True)
f.show()

In [ ]:
# Messages

